# Facial Emotion Recognition using Deep Learning

The goal of the project is to develop a deep learning model that can accurately classify facial expressions into one of six categories: Angry, Disgust, Fear, Happy, Sad, and Surprise. To fulfill the scope of the project we separated the neutral expressions. We will use convolutional neural networks (CNNs) to train our model, as they have been shown to be effective in image classification tasks. Our approach involves training a CNN model from scratch using the FER-2013 dataset.

## Data
The FER-2013 dataset consists of 48x48 pixel grayscale images of faces that have been centered and that occupy a similar amount of space in each image. 

## Importing libraries

Import dataset, assign label, and convert img to array.

In [2]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '0'
import cv2
import numpy as np
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Input, Conv2D, MaxPool2D, Flatten, Dense, Dropout
from keras.callbacks import Callback

# path to folders
dataset_path = 'dataset'

# emotions and respective folders
emotions = ['angry', 'disgust', 'fear', 'happy', 'sad', 'surprise']

def load_img_and_lbl(dataset_type):
    faces = []
    labels = []
    # iterating through file
    for emotion_index, emotion in enumerate(emotions):
        emotion_path = os.path.join(dataset_path, dataset_type, emotion)
        for img_name in os.listdir(emotion_path):
            img_path = os.path.join(emotion_path, img_name)
            
            # load image and convert to grayscale (designed redundantly)
            img = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)
            img = cv2.resize(img, (64,64))
            
            faces.append(img)
            labels.append(emotion_index)
            
    # convert lists to numpyArrays
    faces = np.asarray(faces)
    labels = np.asarray(labels)

    # normalizing images
    faces = faces / 255.0

    # convert labels
    labels = to_categorical(labels, num_classes=len(emotions))
    
    # reshape for modell
    faces = faces.reshape(faces.shape[0], 64, 64, 1)
    
    return faces, labels

# load training- and testdata
x_train, y_train = load_img_and_lbl('train')
x_test, y_test = load_img_and_lbl('test')

print("Form of training data:", x_train.shape, y_train.shape)

Form of training data: (23744, 64, 64, 1) (23744, 6)


In [3]:
from tqdm import tqdm

class TQDMcallBack(Callback):
    def on_train_begin(self, logs={}):
        self.epochs = self.params['epochs']
        self.tqdm_bar = None
        
    def on_epoch_begin(self, epoch, logs={}):
        self.tqdm_bar = tqdm(total=self.params['steps'], desc=f'Epoch {epoch + 1}/{self.epochs}')

    def on_batch_end(self, batch, logs={}):
        if self.tqdm_bar is not None:
            self.tqdm_bar.update(1)
            self.tqdm_bar.set_postfix_str(f"loss: {logs.get('loss', '?')}, acc: {logs.get('accuracy', '?')}")

    def on_epoch_end(self, epoch, logs={}):
        if self.tqdm_bar is not None:
            self.tqdm_bar.close()


def model(input_shape, num_classes):
    model = Sequential([
        Input(shape=input_shape),
        Conv2D(32, kernel_size=(3, 3), activation='relu'),
        MaxPool2D(pool_size=(2, 2)),

        Conv2D(64, kernel_size=(3, 3), activation='relu'),
        MaxPool2D(pool_size=(2, 2)),

        Conv2D(128, kernel_size=(3, 3), activation='relu'),
        MaxPool2D(pool_size=(2, 2)),

        Flatten(),
        Dense(256, activation='relu'),
        Dropout(0.5),
        Dense(num_classes, activation='softmax')
    ])
    model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    return model

#create model
input_shape = (64, 64, 1)
num_classes = len(emotions)
mod = model(input_shape, num_classes)

W0000 00:00:1752832692.835687  849351 gpu_device.cc:2341] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


## Train Model

In [4]:
history = mod.fit(
    x_train, y_train,
    batch_size = 64,
    epochs = 50,
    validation_data=(x_test, y_test),
    callbacks=[TQDMcallBack()]
    )

2025-07-18 11:58:13.257452: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 389021696 exceeds 10% of free system memory.
Epoch 1/50:   0%|          | 0/371 [00:00<?, ?it/s]

Epoch 1/50


Epoch 1/50:   0%|          | 1/371 [00:01<11:44,  1.90s/it, loss: 1.8217626810073853, acc: 0.046875]

  1/371 ━━━━━━━━━━━━━━━━━━━━ 11:44 2s/step - accuracy: 0.0469 - loss: 1.8218

Epoch 1/50:   1%|          | 2/371 [00:02<05:25,  1.13it/s, loss: 1.8017966747283936, acc: 0.1171875]

...

370/371 ━━━━━━━━━━━━━━━━━━━━ 0s 165ms/step - accuracy: 0.9283 - loss: 0.1805

Epoch 50/50: 100%|██████████| 371/371 [01:01<00:00,  6.83it/s, loss: 0.1819079965353012, acc: 0.9273079633712769] 

371/371 ━━━━━━━━━━━━━━━━━━━━ 0s 165ms/step - accuracy: 0.9283 - loss: 0.1805

Epoch 50/50: 100%|██████████| 371/371 [01:05<00:00,  5.71it/s, loss: 0.1819079965353012, acc: 0.9273079633712769]

371/371 ━━━━━━━━━━━━━━━━━━━━ 65s 175ms/step - accuracy: 0.9283 - loss: 0.1805 - val_accuracy: 0.6331 - val_loss: 2.3750


## Evaluate model

In [6]:
test_loss, test_acc = mod.evaluate(x_test, y_test, verbose=2)
print(f'test accuracy: {test_acc}')

186/186 - 3s - 16ms/step - accuracy: 0.6331 - loss: 2.3750
test accuracy: 0.6331371068954468


Save the trained model

In [12]:
mod.save('emotion_recognition_model.keras')

Preprocess random image and load the model to get predictions on new data.

In [16]:
from keras.models import load_model

new_mod = load_model('emotion_recognition_model.keras')

def load_preproc_img(image_path, target_size=(64 ,64)):
    #image to grayscale
    img = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    
    #test if image is loaded properly
    if img is None:
        raise ValueError(f"The image in {image_path} could not be loaded")
    
    # resize
    img = cv2.resize(img, target_size)
    
    #normalizing
    img = img / 255.0
    
    # adjusting form
    img = np.expand_dims(img, axis=-1)
    img = np.expand_dims(img, axis=0)
    
    return img

#path to new img
new_img_path = ('grumpy_baby.jpg')

#load and preprocess
new_img = load_preproc_img(new_img_path)

#calculate prediction
new_pred = new_mod.predict(new_img)

#output
for i, (emotions, prob) in enumerate(zip(emotions, new_pred[0])):
    print(f"{emotions}: {prob * 100:.2f}%")


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 83ms/step

/home/tkr/.local/lib/python3.10/site-packages/keras/src/saving/saving_lib.py:802: UserWarning: Skipping variable loading for optimizer 'rmsprop', because it has 12 variables whereas the saved optimizer has 22 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step
angry: 38.98%
disgust: 0.00%
fear: 0.01%
happy: 42.15%
sad: 18.86%
surprise: 0.00%
